<a href="https://colab.research.google.com/github/vizcayal/Thesis_UT/blob/V1/BASE_CASE_V12.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**Installing packages and Importing libraries**

In [1]:
!pip install gekko
!pip install ipynb
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
import numpy as np
import time
import math
import datetime
from random import sample
from multiprocessing import *
from gekko import GEKKO
import pandas as pd
import random 
import os
from google.colab import files
from google.colab import drive
drive.mount("/content/drive")
import sys
sys.path.append('/content/drive/My Drive/Colab Notebooks/')
start_time = time.time()
# Main Program
 
#Upload distances from each hexagon to other
Hardwood_Saw_Data = pd.read_csv("/content/drive/My Drive/Colab Notebooks/Hardwood_Saw_V7.csv")
Hardwood_Pulp_Data = pd.read_csv("/content/drive/My Drive/Colab Notebooks/Hardwood_Pulp_V7.csv")
Softwood_Saw_Data = pd.read_csv("/content/drive/My Drive/Colab Notebooks/Softwood_Saw_V7.csv")
Softwood_Pulp_Data = pd.read_csv("/content/drive/My Drive/Colab Notebooks/Softwood_Pulp_V7.csv")
Dist_Data = pd.read_csv("/content/drive/My Drive/Colab Notebooks/Dist_Mill.csv")
Cand_Dist = pd.read_csv("/content/drive/My Drive/Colab Notebooks/Candidate_Distance.csv")
Mills_Data = pd.read_csv("/content/drive/My Drive/Colab Notebooks/Mills3.csv")
Factor_Data = pd.read_csv("/content/drive/My Drive/Colab Notebooks/Hexagon_Ratio.csv")
Growth_Data = pd.read_csv("/content/drive/My Drive/Colab Notebooks/Growth_Hexagon_V3.csv")
Growth_Data = Growth_Data[(Growth_Data['OWNERSHIP']=='PRIVATE')&(Growth_Data['SLOPE']=='LE40')] #FILTER OWNERSHIP AND SLOPE
Hexagons = pd.read_csv("/content/drive/My Drive/Colab Notebooks/Hexagons.csv")

i = Mills_Data[Mills_Data.Unique_ID==86399].index #removing this mills with no data
Mills_Data.drop(i, inplace=True)

Dist_Data['DIST'] = Dist_Data['DIST'].replace(0,0.98)   #REPLACE VALUES '0' BY '0.98'
Indices4 = Dist_Data['DEST'].isin(Hexagons.Unique_ID)
Dist_Data = Dist_Data.loc[Indices4,:]
Dist_Data.reset_index(inplace = True, drop = True)

Cand_Dist = pd.read_csv("/content/drive/My Drive/Colab Notebooks/Candidate_Distance_v2.csv")
Cand_Dist['DIST'] = Cand_Dist['DIST'].replace(0,0.98)   #REPLACE VALUES '0' BY '0.98'
Indices5 = Cand_Dist['DEST'].isin(Hexagons.Unique_ID)
Cand_Dist = Cand_Dist.loc[Indices5,:]
Cand_Dist.reset_index(inplace = True, drop = True)

FOREST_INVENTORY = []
FOREST_INVENTORY.append(np.sum(Hardwood_Saw_Data.SumOfTotal))
FOREST_INVENTORY.append(np.sum(Hardwood_Pulp_Data.SumOfTotal))
FOREST_INVENTORY.append(np.sum(Softwood_Saw_Data.SumOfTotal))
FOREST_INVENTORY.append(np.sum(Softwood_Pulp_Data.SumOfTotal))


     |████████████████████████████████| 10.8MB 5.9MB/s 


KeyboardInterrupt: ignored

**SAWMILL CLASS**

In [ ]:
DISTANCE_MODE = 1                               #Harvesting mode that reach closest locations
DENSITY_MODE = 2                                #Harvesting mode that reach more dense locations
ECONOMIC_MODE = 3                               #Harvesting mode that reach less expensive locations considering hauling costs and harvesting costs
FOLDER_NAME = '/content/drive/My Drive/Colab Notebooks/Results/'
CF_TO_DT = 0.01814*0.55                         #dt/cf   
STUMPAGE_COST = [34,17,32,16]                   #$/Ton [Hardwod Sawtimber, Hardwood Pulpwood, Softwood Sawtimber, Softwood Pulpwood]
STUMPAGE_COST_RES = 8.25                   #$/Ton [Hardwod Sawtimber, Hardwood Pulpwood, Softwood Sawtimber, Softwood Pulpwood]
HARVESTING_COST = [368.1,363.5,152.1,158.8]     #$/Acre
HARVESTING_COST_RES = 0.1*sum([FOREST_INVENTORY[i] * HARVESTING_COST[i] for i in range(len(FOREST_INVENTORY))])/sum(FOREST_INVENTORY) #Harvesting cost for residues is calculated as 10% the weight average of harvest cost for 1st stage
HAULING_COST = 0.271
BIOFUEL_HAULING_COST = 0.00017                  #$/gal/mi
AIRPORT_LOCATION = 78006                        #Number of the Hexagon where the refinery is located
STUMPAGE_COST_RES = 8.25                        #$/Ton [Hardwod Sawtimber, Hardwood Pulpwood, Softwood Sawtimber, Softwood Pulpwood]
HAULING_COST_RES = 0.31                        #$/ton/mi 
CONV_COST = 0.72
YEARS = 10
MAX_MILLS = 500

CASE = 2
CASE_IN = 1

CONV_YIELD = 70
AIRPORT_DEMAND = 96000000
PERC_DEMAND = 0.20
RADIO_MILL = 100                                #Radio distance from mills 
RADIO_REFINERY = 100                            #Radio distance from mills 
RESIDUES_LEFT = 0.3                             #Percentage residues left in the ground
COMMERCIAL_PERC = 0.338
NIPS_PERC =0.64
FILE_NAME_OUT = 'C'+str(CASE)+'_'
WILLING_NIPS = 0.45
INTEREST_RATE = 0.1

DEPRECIATION_RATE = [(1+INTEREST_RATE)**h for h in range(1,YEARS+1)]

if CASE == 1:
  HARVESTING_MODE = DISTANCE_MODE
  CASE_IN = 1

elif  CASE== 2:
  HARVESTING_MODE = DISTANCE_MODE
  CASE_IN = 1
  WILLING_NIPS = 0.38

elif  CASE== 3:
  HARVESTING_MODE = DISTANCE_MODE
  CASE_IN = 1
  WILLING_NIPS = 0.65

if CASE == 4:
  HARVESTING_MODE = DISTANCE_MODE
  CASE_IN = 1
  CONV_YIELD = 60

if CASE == 5:
  HARVESTING_MODE = DISTANCE_MODE
  CASE_IN = 1
  CONV_YIELD = 80


elif  CASE== 8:
  HARVESTING_MODE = DENSITY_MODE
  CASE_IN = 8

elif  CASE== 9:
  HARVESTING_MODE = DENSITY_MODE
  CASE_IN = 8
  WILLING_NIPS = 0.38

elif  CASE== 10:
  HARVESTING_MODE = DENSITY_MODE
  CASE_IN = 8
  WILLING_NIPS = 0.65

elif CASE == 11:
  HARVESTING_MODE = DENSITY_MODE
  CASE_IN = 8
  CONV_YIELD = 60

elif CASE == 12:
  HARVESTING_MODE = DENSITY_MODE
  CASE_IN = 8
  CONV_YIELD = 80


elif  CASE== 15:
  HARVESTING_MODE = ECONOMIC_MODE
  CASE_IN = 15

elif  CASE== 16:
  HARVESTING_MODE = ECONOMIC_MODE
  CASE_IN = 15
  WILLING_NIPS = 0.38

elif  CASE== 17:
  HARVESTING_MODE = ECONOMIC_MODE
  CASE_IN = 15
  WILLING_NIPS = 0.65

elif CASE == 18:
  HARVESTING_MODE = ECONOMIC_MODE
  CASE_IN = 15
  CONV_YIELD = 60

elif CASE == 19:
  HARVESTING_MODE = ECONOMIC_MODE
  CASE_IN = 15
  CONV_YIELD = 80


FILE_NAME_IN = 'C'+str(CASE_IN)+'_'
REF_DEMAND = int(AIRPORT_DEMAND * PERC_DEMAND / CONV_YIELD)
WILLING_FACTOR = NIPS_PERC*WILLING_NIPS + COMMERCIAL_PERC #Willingness to harvest factor

class Inventory:
  Total_Harvested = []                              #Total Wood harvested in the first stage. used to determine forest residues
  Total_Residues = []                               #Forest Residues Generated in each year
  Total_Acum_Residues = []                          #Residues acumulated through the studied period equals residues from last month plus residues in the present month minus residues harvested 
  Res_Harvested = []                                #Residues Harvested by the refinery in each year in the second stage
  Total_Cost = []                                   #Harvesting costs in the first stage by year
  Total_Cost_Res = []                               #Harvesting cost in the second stage by cand and year
  Cand_Cost = pd.DataFrame() 

  def __init__(self, Av, Dist, Typ,Wt=-1, Pt=-1,Name ="", Willingness = 1,Factors = [],St = 1):
    self.AcumResidues = []                          #Residues generated by harvesting
    self.Available = list()
    self.Available.append(Av.copy())                #Dataframe that contains Available wood Inventory at diferent time t
    self.Available[0].loc[:,('SumOfTotal')] = self.Available[0].loc[:,('SumOfTotal')] * Willingness
    self.Available_Mill = []                        #Dataframe that contains the Available Inventory close the mill to be harvested
    self.By_Mill = []                               #Quantity harvested by each mills in each hexagon
    self.By_Cand_Harv = []                          #Quantity harvested by each Cand in each hexagon
    self.By_Cand_Avail = []                         #Quantity Available for each mills in each hexagon
    self.Candidates=[]                              #Candidate location for biorefinery
    self.Costs_1st = []
    self.Costs_2nd = []
    self.Harvest_Cost=[]                            #annual cost for 1st stage
    self.Harv_Cost_Per_Unit =HARVESTING_COST[Typ]   #annual cost for 1st stage
    self.Stumpage_Cost_Per_Unit = STUMPAGE_COST[Typ]   #annual cost for 1st stage
    self.Dist = Dist                                #Matrix Distance from any Mills or candidates cells to other cells
    self.Dist_Mill = []                             #Dataframe that contains the Distance to the specific mill
    self.Dist_Refi = []                             #Dataframe that contains the Distance to the refinery 
    self.Harvested = []                             #Ammount of harvested wood
    self.Harvested_Res = []                         #Amoun of Residues Harvested
    self.Name = Name                                #Name of the layer
    self.ProdType = Pt                              #type of product generated (pulp or saw)
    self.RefCost = []                               #Matrix Distance from any Mills and candidates cells to other cells
    self.Residues = []                              #Residues generated by harvesting mills
    self.Residues_Left = 0.30                       #Portion of residues left in the ground and not used for the biorefinery
    self.Results_2nd = []
    self.St =St                                     #stage run, there is two stages in the model stage 1 is modeling the supply of mills, stage 2 is locating the refinery 
    self.Typ =Typ                                   #type of wood Hardwod Sawtimber = 0 , Hardwood Pulpwood = 1, Softwood Sawtimber = 2 , Softwood Pulpwood = 3 ]
    self.Willingness = Willingness                  #portion of timber available for residues.
    self.WoodType = Wt                              #type of wood needed (softwood, hardwood)
    
    self.Available[0].SumOfTotal =self.Available[0].SumOfTotal * self.Willingness #applying willingness to harvest
    
    Id_li = list(self.Available[0].loc[:,("Unique_ID")])
    r1 = len(self.Available[0])
    Ha_li =[0]*r1
    Data = {'Unique_ID':Id_li}
    self.By_Mill =pd.DataFrame(Data).copy()
    
    Data = {'Unique_ID':Id_li,'Harvested':Ha_li}
    self.Harvested.append(pd.DataFrame(Data).copy())
    Data = {'Unique_ID':Id_li,'Growth':Ha_li}
    self.Growth =pd.DataFrame(Data).copy()    
    self.Factors = self.Available[0].merge(Factors, on='Unique_ID',how = 'left')
    pd.set_option("display.max_rows", 2000, "display.max_columns", 5)
    

  def Harvest_All_Mills(self,t,k,mode = DISTANCE_MODE):
  #Harvest k mills at year t for the first stage in year t
    self.Available.append(self.Available[t].copy())
    for i in range(k):
      print('Cosechando Sawmill:',i)
      self.Harvest_Mill(t,i,mode)
 
    self.Harvested.append(self.Harvested[t].copy()) 
    self.Harvested[t+1].loc[:,('Harvested')] = 0
    self.Residues.append(self.Harvested[t].loc[:,('Unique_ID','Harvested')].copy())
    Rati = self.Residues[t].merge(self.Factors, on='Unique_ID',how = 'left')
    self.Residues[t].loc[:,('Harvested')] = self.Residues[t].loc[:,('Harvested')]*Rati.Ratio #substract the portion of residues left in the ground
    self.Residues[t].loc[:,('Harvested')] = self.Residues[t].loc[:,('Harvested')]*self.Factors.loc[:,('Ratio')] #substract the portion of residues left in the ground
    self.Residues[t].loc[:,('Harvested')] = self.Residues[t].loc[:,('Harvested')]*(1-RESIDUES_LEFT) #substract the portion of residues left in the ground
    self.Residues[t].loc[:,('Harvested')] = round(self.Residues[t].loc[:,('Harvested')]*CF_TO_DT) #transforming CF to Dry Tons
    print('Residues:',np.sum(self.Residues[t].Harvested))


  def Add_Growth(self,t):
    #increase the available inventory of period t
    self.Available[t].loc[:,("SumOfTotal")] = self.Available[t].loc[:,("SumOfTotal")]+self.Growth['Growth']


  def Initialize_Totals(self,Y):
    self.__class__.Total_Harvested = []
    self.__class__.Total_Residues = []
    for i in range(Y+1):
      self.__class__.Total_Harvested.append(pd.DataFrame({'Unique_ID' : [],'Harvested':[]})) #initialize Total Harvested variable (for all the layers)
      self.__class__.Total_Residues.append(pd.DataFrame({'Unique_ID' : [],'Harvested':[]})) #Initialize Total Residues variable (for all the layers)
    self.__class__.Total_Cost = [0]*Y
    self.__class__.Total_Cost_Res = [0]*Y
    

  def Total_Harvested_Update(self,Y):
    for i in range(Y):
      self.Harvested[Y].loc[:,('Harvested')] = self.Harvested[Y].loc[:,('Harvested')] + self.Harvested[i].loc[:,('Harvested')]
    for i in range(Y+1):
      c = pd.concat([self.__class__.Total_Harvested[i], self.Harvested[i]]).groupby(['Unique_ID']).sum().reset_index() #updating Total Harvested
      self.__class__.Total_Harvested[i] = c.copy()


  def Total_Residues_Update(self,Y):
    for i in range(Y):
      self.Residues[Y].loc[:,('Harvested')] = self.Residues[Y].loc[:,('Harvested')] + self.Residues[i].loc[:,('Harvested')]
 
    for i in range(Y+1):
      c = pd.concat([self.__class__.Total_Residues[i], self.Residues[i]]).groupby(['Unique_ID']).sum().reset_index() #Acumulate Residues from other layers
      self.__class__.Total_Residues[i] = c.copy()
      #print('Available resources at:',i,np.sum(self.__class__.Total_Residues[i].Harvested))
 

  def Harvest_All_Mills_All_Years(self,Y,mode=DISTANCE_MODE):
    Max = MAX_MILLS
    Min = 1    
    N_Mills = len(self.Mills)
    if (N_Mills>Max):
      N_Mills = Max
    if (N_Mills<Min):
      N_Mills = Min
    
    self.Harvest_Cost=[0]*Y

    now = datetime.datetime.now()
    for y in range(Y):
      start_time1 = time.time()
      self.Costs_1st.append([0]*5)
      self.Harvest_All_Mills(y,N_Mills,mode)
      self.Add_Growth(y)
      self.By_Mill.to_csv(FOLDER_NAME+'DETAILS/'+FILE_NAME_OUT+self.Name+'_ByMills'+'_'+str(now.day)+'_'+' year'+str(y)+'.csv')  
      print ("*********1ST STAGE YEAR: ",str(y),' TOOK', time.time() - start_time1, "TO RUN") 

    self.Residues.append(self.Residues[0].loc[:,('Unique_ID','Harvested')].copy())
    self.Residues[Y].loc[:,('Harvested')] = 0
    pd.DataFrame(self.Costs_1st).to_csv(FOLDER_NAME+FILE_NAME_OUT+self.Name + '_COST_YEAR.csv')  

 
  def Growth_Update(self,Data):
    N = len(self.Growth)
    if self.ProdType == 'Sawmill':
      cl = 1
    elif self.ProdType == 'Pulpmill':
      cl =2
    Data = Data[Data['CLASS'] == cl]
    for i in range(N):    
      Id = self.Growth.loc[i,("Unique_ID")]
      Row = Data[Data['Unique_ID'] == Id]
      if not Row.empty:
        if self.WoodType == 'H':
          self.Growth.loc[i,('Growth')] = Row.iloc[0,4] + Row.iloc[0,5] + 0.33 * Row.iloc[0,8]
        if self.WoodType == 'S':
          self.Growth.loc[i,('Growth')] = Row.iloc[0,6] + Row.iloc[0,7] + 0.67 * Row.iloc[0,8]


  def Cell_Less_Res(self, Id_Mill, t, Radio):
    #Given Time, Radio and a Mill ID this function returns a Dataframe of cells with Distance and Forest Residues available
    Ans = Cand_Dist[(Cand_Dist['ORIG'] == Id_Mill)&(Cand_Dist['DIST'] <= Radio)] #CELLS EQUAL ID_MILL AND CLOSER THAN RADIO
    Ans.sort_values(by="DEST",inplace = True)
    Indices = Ans["DEST"].isin(self.__class__.Total_Acum_Residues[t].Unique_ID)
    Ans = Ans.loc[Indices,:]
    Ans.reset_index(inplace = True, drop = True)
    Indices2 = self.__class__.Total_Acum_Residues[t]["Unique_ID"].isin(Ans["DEST"])
    Ans.loc[:,("AVAIL")] = list(self.__class__.Total_Acum_Residues[t].loc[Indices2,('Harvested')] )
    Ans.reset_index(inplace = True, drop = True)
    return(Ans)
 
  
  def Cell_Less(self, Id_Mill, t, Radio=  RADIO_MILL):
    #Given Time, Radio and a Mill ID this function returns a list of cells with Distance and Availability
    Ans = self.Dist[(self.Dist['ORIG'] == Id_Mill)&(self.Dist['DIST'] <= Radio)] #Look for in Dist matrix cell with the ID and closer than Radio
    Ans.sort_values(by="DEST",inplace = True)
    Indices = Ans["DEST"].isin(self.Available[t].Unique_ID)
    Ans = Ans.loc[Indices,:]
    Ans.reset_index(inplace = True, drop = True)
    Indices2 = self.Available[t]["Unique_ID"].isin(Ans["DEST"])
    Ans.loc[:,("AVAIL")] = list(self.Available[t].loc[Indices2,('SumOfTotal')] )
    Ans.loc[:,("AVAIL")] = list(self.Available[t].loc[Indices2,('SumOfTotal')] )
    Indices3 = Ans.loc[:,("AVAIL")]==0
    Ans.loc[Indices3,('AVAIL')]=0.01
    Ans.reset_index(inplace = True, drop = True)    
    return(Ans)


  def Mills_Update(self,M):
    i1 = (M['s_h'] == self.WoodType)&(M['plant'] == self.ProdType)
    self.Mills = M.loc[i1,:]
    Num = len(self.Mills)
    ind = [i for i in range(Num)]
    self.Mills.index = ind
 

  def Total_Available(self, Id_Mill,t, Radio=RADIO_MILL):
    #Given a Radio and a Mill ID this function returns a the total inventory Available
    Ans = self.Dist[(self.Dist['ORIG'] == Id_Mill)&(self.Dist['DIST'] <= Radio)] #CELLS EQUAL ID_MILL AND CLOSER THAN RADIO
    rows = Ans.shape[0]
    ind = [i for i in range(rows)]
    Ans.index=ind    
    Disp =[]
    for j in range(len(Ans)):
      if self.Available[t][self.Available[t]["Unique_ID"]==Ans.loc[j,('DEST')]].empty:
        Disp.append(0)
      else:
        Disp.append(int(self.Available[t][self.Available[t]["Unique_ID"]==Ans.loc[j,('DEST')]].SumOfTotal.copy()))
    Total = np.sum(Disp)
    return(Total)
 
 
  def List_Available(self,t,L): #Given a list L of ID, the funtion returns a List of Availability
    Indices2 = self.Available[t]["Unique_ID"].isin(L)
    Av1 = self.Available[t].loc[Indices2,('SumOfTotal')] 
    Av1.reset_index(inplace = True, drop = True)
    return(list(Av1))


  def List_Available_Res(self,t,L): #Given a list L of ID, the funtion returns a List of Availability
    Indices2 = self.__class__.Total_Acum_Residues[t]["Unique_ID"].isin(L)
    Av1 = self.__class__.Total_Acum_Residues[t].loc[Indices2,('Harvested')] 
    Av1.reset_index(inplace = True, drop = True)
    return(list(Av1))


  def Initial_Total_Res(self,Y,L): #Given a list L of ID, the funtion returns a Initial Availability at year Y
    Indices2 = self.__class__.Total_Residues[Y]["Unique_ID"].isin(L)
    Av1 = self.__class__.Total_Residues[Y].loc[Indices2,('Harvested')] 
    Av1.reset_index(inplace = True, drop = True)
    return(list(Av1))


  def Residues_Produced(self,t,L): #Given a list L of ID, the funtion returns a List of Availability
    Av = []
    for id in L:
      if self.__class__.Total_Residues[t][self.__class__.Total_Residues[t]["Unique_ID"]==id].empty:
        Av.append(0)
      else:
        a1 = int(self.__class__.Total_Residues[t][self.__class__.Total_Residues[t]["Unique_ID"]==id].Harvested)  
        Av.append(a1)
    return(Av)


  def Load_Residues(self,Y): #Given the number of years the residues are loaded from files
    for y in range(Y+1):
      self.__class__.Total_Residues[y]= pd.read_csv(FOLDER_NAME+FILE_NAME_IN+'RESIDUES_'+str(y)+'.csv')


  def Evaluate_Potencial(self,Y): 
    Potential = [] #list of list to store year/mill/available/cost/
    Num = len(self.Candidates)
    
    for c in range(Num):
      print('Cand', c)
      Id1 =self.Candidates[c] #assign unique ID
      a =self.Cell_Less_Res(Id1,0,RADIO_REFINERY) #look for hexagons between radio distance
      Id_list = a.loc[:, ('DEST')]
      self.Dist_Refi = a.loc[:, ('DIST')]  #obtain column Distance from 'a'
        
      for y in range(Y): #harvesting each mill from year 1 to Y
        Res_Year =[0]*4
        Res_Year[0] = Id1 #storing Mill Id
        Res_Year[1] = y   #storing year  
        self.Available_Refi  = self.Residues_Produced(y,Id_list)
        Res_Year[2] = sum(self.Available_Refi)   #storing year
        cost = self.Available_Refi @ self.Dist_Refi
        Res_Year[3] = cost   #storing year
        Potential.append(Res_Year)
    pd.DataFrame(Potential).to_csv(FOLDER_NAME+FILE_NAME_OUT+'POTENCIAL_CAND.csv')  


  def Optimal_Location_Total2(self,Y, Part ,Demand = 10000): 
    #run Ncan locations from year 0 to year 'y'
    Id_li = list(self.__class__.Total_Residues[0].loc[:,("Unique_ID")])
    r1 = len(self.__class__.Total_Residues[0])
    Ha_li =[0]*r1
    Data = {'Unique_ID':Id_li,'Harvested':Ha_li}    
    self.Harvested_Res.append(pd.DataFrame(Data).copy())
    Data = {'Unique_ID':Id_li}   
    self.By_Cand_Harv =pd.DataFrame(Data).copy()
    self.By_Cand_Avail =pd.DataFrame(Data).copy()
    self.Harvested_Res.append(pd.DataFrame(Data).copy())
    Harv_List=[] #list of list to store harvested amount in each year
    Result_2nd = [] #list of list to store mill/available/cost/demand for each year
    Num = len(self.Candidates)
    #Num2 = Num//2
        
    #if self.St ==1:
    #  self.Candidates = self.Candidates[:Num2]
    #  print('self.candidates ', self.Candidates)

    #if self.St ==2:
    #  self.Candidates = self.Candidates[Num2+1:]
    
    print('self.candidates ', self.Candidates)
    L_Cand = range(len(self.Candidates))


    for y in range(Y):
      Harv_List.append(Ha_li)    

    self.RefCost = [0]*len(L_Cand)
 
    for c in range(len(L_Cand)):
      Ha_li =[0]*Y
      self.__class__.Total_Acum_Residues = []
      self.__class__.Total_Acum_Residues.append(self.__class__.Total_Residues[0].copy())
      self.__class__.Total_Acum_Residues[0].loc[:,('Harvested')] = 0
      self.__class__.Total_Cost_Res = [0]*Y
      Id1 =self.Candidates[c] #assign unique ID
      print('Cand', c,' Cod ', Id1)
      
      a =self.Cell_Less_Res(Id1,0,RADIO_REFINERY) #look for hexagons between radio distance
      self.Dist_Refi = a.loc[:, ('DEST','DIST')] 
      start_time_cand = time.time()
      Stop = False  
      
      for i in range(Y): #harvesting each mill from year 1 to Y

        self.__class__.Total_Acum_Residues.append(self.__class__.Total_Acum_Residues[i].copy())
        self.__class__.Total_Acum_Residues[i+1].loc[:,('Harvested')] =self.__class__.Total_Acum_Residues[i+1]['Harvested'] + self.__class__.Total_Residues[i]['Harvested'].copy()
        self.Harvested_Res[i].loc[:,('Harvested')] = 0
        Id_list = list(self.Dist_Refi.loc[:, ('DEST')])
        Avail_Aux  = np.sum(self.List_Available_Res(i+1,Id_list))
        print('Disponible: ', Avail_Aux, ' Demanda: ', Demand)
        if Avail_Aux >= Demand:
          self.Harvest_Refinery(i,c,Demand)
        else:
          break
        self.__class__.Total_Acum_Residues[i+1].loc[:,("Harvested")] = self.__class__.Total_Acum_Residues[i+1].loc[:,("Harvested")] - self.Harvested_Res[i].loc[:,('Harvested')].copy()
        self.By_Cand_Harv[i] = self.Harvested_Res[i].loc[:,('Harvested')].copy()
        self.By_Cand_Avail[i] = self.__class__.Total_Acum_Residues[i+1].loc[:,('Harvested')].copy()
        self.Harvested_Res.append(self.Harvested_Res[i].copy())     
        self.Harvested_Res[i+1].loc[:,('Harvested')] = 0
        self.__class__.Cand_Cost.loc[:,(str(c))] =self.__class__.Total_Cost_Res.copy()
          
        
      print ("*********CAND ",str(c),' Took ', time.time() - start_time_cand, " TO RUN")
        
      pd.DataFrame(self.By_Cand_Harv).to_csv(FOLDER_NAME+'DETAILS/'+FILE_NAME_OUT+'CAND_'+str(Id1)+'RES_HARVESTED.csv')  
      pd.DataFrame(self.By_Cand_Avail).to_csv(FOLDER_NAME+'DETAILS/'+FILE_NAME_OUT+'CAND_'+str(Id1)+'RES_AVAILABLE.csv')  
    pd.DataFrame(self.Results_2nd).to_csv(FOLDER_NAME+FILE_NAME_OUT+'_St_'+str(self.St)+'_RESULTS_2ND.csv')  


  def Harvest_Refinery(self,t,Cand, Ref_Demand): #Evaluates Candidate location for refinery in year t
    m2 = GEKKO(remote=True)
    m2.options.solver = 3 #IPOPT solver
    m2.options.IMODE = 3 #steady state optimization
    Res_Year =[0]*9
    Id1 =self.Candidates[Cand] #assign unique ID
    Res_Year[0] = Id1 #storing Mill Id
    Res_Year[1] = t   #storing year
    Ind_Airport = (Cand_Dist['ORIG']== Id1) & (Cand_Dist['DEST']== AIRPORT_LOCATION)  
    Dist_Airport = float(Cand_Dist.loc[Ind_Airport,('DIST')])    
    Id_list = list(self.Dist_Refi.loc[:, ('DEST')])
    self.Available_Refi  = self.List_Available_Res(t+1,Id_list)
    
    Total_Res_Produced = self.Initial_Total_Res(YEARS,Id_list)
    Total_Res_Produced = [0.01  if Total_Res_Produced[i] == 0 else Total_Res_Produced[i]  for i in range(len(Total_Res_Produced)) ]
    Num = len(self.Dist_Refi) #calculate the number of cells betwee 
  
    H = m2.Array(m2.Var,(Num),value = 0)
    Res_Year[2] = np.sum(self.Available_Refi) #storing availability
   
    for i in range(Num):
      H[i].lower = 0
      H[i].upper = self.Available_Refi[i]  

    BIOFUEL_COST = Dist_Airport * BIOFUEL_HAULING_COST * AIRPORT_DEMAND * PERC_DEMAND
    prod0 = m2.Intermediate(m2.sum([(STUMPAGE_COST_RES + HAULING_COST_RES * self.Dist_Refi.loc[i,('DIST')] + 5 * HARVESTING_COST_RES / Total_Res_Produced[i] + 0.72 *CONV_YIELD ) * H[i] / DEPRECIATION_RATE[t]   for i in range(Num)]))
    
    m2.Equation(Ref_Demand ==m2.sum([H[i] for i in range(0,len(H))]))
    m2.Obj(prod0) 
    m2.solve(disp=False,debug=False)
    flat = [item for l in H for item in l]
    Harvested = np.sum(flat)                                          #AMOUNT HARVESTED
    Res_Year[3] = np.sum(flat)                                        #AMOUNT HARVESTED
    self.Harvested_Res[t].loc[:,('Harvested')]=0
    ans = self.Dist_Refi.copy()
    ans['Harvested'] = flat

    ans.reset_index(inplace = True)    
    ans.rename(columns={ 'DEST' : 'Unique_ID'},  inplace=True)
    ans.set_index('Unique_ID', inplace = True)
    Id_li = list(self.Harvested_Res[0].loc[:,("Unique_ID")])
    r1 = len(self.Harvested_Res[0])
    Ha_li =[0]*r1
    Data = {'Unique_ID':Id_li,'Harvested':Ha_li}
    Aux =pd.DataFrame(Data).copy()
    Aux.set_index('Unique_ID', inplace = True)
    Aux.update(ans)
    Aux.reset_index(inplace = True)
    self.Harvested_Res[t].Harvested = self.Harvested_Res[t].Harvested.add(Aux.Harvested,fill_value=0)
    res = np.sum(flat*self.Dist_Refi.loc[:,('DIST')]) * HAULING_COST_RES #Delivery cost to refinery
    self.__class__.Total_Cost_Res[t] += res * HAULING_COST_RES
    self.RefCost[Cand] += res * HAULING_COST_RES 
    print('Cost:', self.RefCost[Cand], ' Year: ',t)
    
    Ar = np.divide(flat , Total_Res_Produced)*5
    Ar = pd.Series(Ar).fillna(0).tolist()
    Ar= np.sum(Ar)
    
    Res_Year[4] = Harvested * STUMPAGE_COST_RES           #STUMPAGE COSTS
    Res_Year[5] = np.sum(flat*self.Dist_Refi.loc[:,('DIST')]) * HAULING_COST_RES                                         #FEEDSTOCK TRANPORTATION COST                  #HARVESTING COSTS
    Res_Year[6] = Ar *HARVESTING_COST_RES*640                                         #FEEDSTOCK TRANPORTATION COST
    Res_Year[7] = AIRPORT_DEMAND * CONV_COST * PERC_DEMAND    #CONVERSION COST 
    Res_Year[8] = BIOFUEL_COST                                #BIOFUEL TRANPORTATION  COST
    
    print('Resultados: ',Res_Year)

    self.Results_2nd.append(Res_Year)



  def Harvest_Mill(self,t, j,mode=DISTANCE_MODE):
    #Given a period t and a Mill j the function provide the harvested wood and substract it from available inventory
    m = GEKKO(remote=True)
    m.options.solver = 3                        #IPOPT solver
    m.options.IMODE = 3                         #steady state optimization
    Dem = self.Mills.loc[j,('Demand')]
    Id1 =self.Mills.loc[j,('Unique_ID')]        #look for mill in position j
    Name_Mill =self.Mills.loc[j,('Name')]       #look for mill in position j
    Rad = 10
    Ready = False
    r = 1
    
    if mode == DENSITY_MODE:  #In case of Density Criteria the dataframe is sort by availability
      b =self.Cell_Less(Id1,t+1,RADIO_MILL)
      Id_list = b.loc[:, ('DEST')]
      Num = len(b)
      b['Available_At_0']  = self.List_Available(0,Id_list)
      b['Per_Unit_Total_Cost'] = [5 * 640 * self.Harv_Cost_Per_Unit / b['Available_At_0'][i] / DEPRECIATION_RATE[t] if (b['Available_At_0'][i]>0) else 1000000000 for i in range(Num)]
      b.sort_values(by='Per_Unit_Total_Cost',inplace = True, ascending = True)
      b.reset_index(inplace = True, drop = True)
      

    elif mode == DISTANCE_MODE:
      while((Rad<=RADIO_MILL) & (not Ready)):
        b =self.Cell_Less(Id1,t+1,Rad)
        self.Available_Mill  = b.loc[:, ('AVAIL')]
        self.Dist_Mill = b.loc[:, ('DEST','DIST')]  #fill Distances to mills
        Num = len(self.Dist_Mill)
        Id_list = b.loc[:, ('DEST')]
        b['Available_At_0']  = self.List_Available(0,Id_list)
        b['Per_Unit_Total_Cost'] = [HAULING_COST * CF_TO_DT * self.Dist_Mill.loc[i,('DIST')] / DEPRECIATION_RATE[t] for i in range(Num)]
        self.Available_Mill  = b.loc[:, ('AVAIL')]
        D1 = np.sum(self.Available_Mill)
        if D1 >= Dem:
          Ready = True
          r = len(b)
        else:
          Rad +=10
      b.sort_values(by='DIST',inplace = True)
      b.reset_index(inplace = True)
    
    elif mode == ECONOMIC_MODE:
      b =self.Cell_Less(Id1,t+1,RADIO_MILL)
      Id_list = b.loc[:, ('DEST')]
      self.Available_Mill  = b.loc[:, ('AVAIL')]
      self.Dist_Mill = b.loc[:, ('DEST','DIST')]  #fill Distances to mills
      Num = len(self.Dist_Mill)
      b['Available_At_0']  = self.List_Available(0,Id_list)
      b['Per_Unit_Total_Cost'] = [5 * 640 * self.Harv_Cost_Per_Unit / b['Available_At_0'][i] + CF_TO_DT * HAULING_COST * self.Dist_Mill.loc[i,('DIST')] / DEPRECIATION_RATE[t] if (b['Available_At_0'][i]>0) else 1000000000 for i in range(Num)]
      b.sort_values(by='Per_Unit_Total_Cost',inplace = True, ascending = True)
      b.reset_index(inplace = True, drop = True)  
      
    a = b.iloc[:r,:]         #look for cells with radio less than rad.
    self.Dist_Mill = a.loc[:, ('DEST','DIST')]  #fill Distances to mills
    Id_list = a.loc[:, ('DEST')]
    c  =self.Available_Mill  = b.loc[:, ('DEST','AVAIL')]
    self.Available_Mill = c[:r]
    D1 = np.sum(self.Available_Mill.AVAIL)
    
    while (D1<=Dem): #expand the number of cells until inventory available is greater than demand
      r +=10
      a = b.iloc[:r,:]         #Expanding the number of cells to reach availability greater than demand.
      self.Dist_Mill = a.loc[:, ('DEST','DIST')]  #fill Distances to mills
      Id_list = a.loc[:, ('DEST')]
      c  = a.loc[:, ('DEST','AVAIL')]
      self.Available_Mill = c[:r]
      D1 = np.sum(self.Available_Mill.AVAIL)
    
    print('Inventory: ',self.Name,' Year: ',t, 'Mill: ',Id1,'**Demanda:', Dem, 'Disponible',D1,  "Radio",Rad )  
    
    Num = len(self.Dist_Mill)
    H = m.Array(m.Var,(Num),value = 0)
    r1 = len(self.Available[0])
    Ha_li =[0]*r1
    self.By_Mill[Name_Mill] = Ha_li
      
    for i in range(Num):
      H[i].lower = 0
      H[i].upper = self.Available_Mill.AVAIL[i]

    self.Per_Unit_Total_Cost = a.Per_Unit_Total_Cost
    prod0 = m.Intermediate(m.sum([self.Per_Unit_Total_Cost[i]*H[i] for i in range(Num)]))
 
    m.Equation(Dem ==m.sum([H[i] for i in range(0,len(H))]))
    m.Obj(prod0) 
    Sol = m.solve(disp=False,debug=False)
    print('Solution',Sol)
    flat = [item for l in H for item in l]
    
    ans= self.Dist_Mill
    ans['Harvested'] = flat
    ans.reset_index(inplace = True)    
    ans.rename(columns={ 'DEST' : 'Unique_ID'},  inplace=True)
    ans.set_index('Unique_ID', inplace = True)
    Id_li = list(self.Available[0].loc[:,("Unique_ID")])
    r1 = len(self.Available[0])
    Ha_li =[0]*r1
    Data = {'Unique_ID':Id_li,'Harvested':Ha_li}
    Aux =pd.DataFrame(Data).copy()
    Aux.set_index('Unique_ID', inplace = True)
    Aux.update(ans)
    Aux.reset_index(inplace = True)
    self.Harvested[t].Harvested = self.Harvested[t].Harvested.add(Aux.Harvested,fill_value=0)
    self.Available[t+1].loc[:,("SumOfTotal")] = self.Available[t+1].loc[:,("SumOfTotal")] - Aux.loc[:,("Harvested")]
    
    Costs = [0,0,0,0]
    Costs[1] = Dem * STUMPAGE_COST[self.Typ]  * CF_TO_DT               #STUMPAGE COSTS
    Ar = np.divide(flat , a['Available_At_0'])*5
    Ar = pd.Series(Ar).fillna(0).tolist()
    Ar= np.sum(Ar)
    Costs[2] = Ar * HARVESTING_COST[self.Typ] *640      #harvesting costs proportional to the harvested area
    Mill_Cost = np.sum(flat * self.Dist_Mill.DIST)
    Costs[3] = Mill_Cost * HAULING_COST  * CF_TO_DT          #Hauling costs
    Costs = np.nan_to_num(Costs)
    self.Costs_1st[t][0] = Ar
    self.Costs_1st[t][1] = self.Costs_1st[t][1]+ Costs[1] 
    self.Costs_1st[t][2] = self.Costs_1st[t][2]+ Costs[2] 
    self.Costs_1st[t][3] = self.Costs_1st[t][3]+ Costs[3] 
    
    self.Costs_1st[t][4] += (Costs[1]+ Costs[2]+ Costs[3]) / DEPRECIATION_RATE[t]                        
    self.__class__.Total_Cost[t]  += (Costs[1]+ Costs[2]+ Costs[3]) / DEPRECIATION_RATE[t]                        #Accumulated Costs





**1ST PHASE - MILLS DEMAND - SHORTEST DISTANCE CRITERIA**


In [ ]:
start_time = time.time()
print("Creating Inventories Objects and Initializing...")
Hardwood_Saw = Inventory(Hardwood_Saw_Data,Dist_Data,Wt='H',Pt ='Sawmill', Name = "Hardwood_Saw_v3", Willingness = WILLING_FACTOR,Factors =Factor_Data,Typ =0)
Hardwood_Pulp = Inventory(Hardwood_Pulp_Data,Dist_Data,Wt='H',Pt ='Pulpmill', Name = "Hardwood_Pulp_v3", Willingness = WILLING_FACTOR,Factors =Factor_Data, Typ =1)
Softwood_Saw = Inventory(Softwood_Saw_Data,Dist_Data,Wt='S',Pt ='Sawmill', Name = "Softwood_Saw_v3", Willingness = WILLING_FACTOR,Factors =Factor_Data, Typ = 2)
Softwood_Pulp = Inventory(Softwood_Pulp_Data,Dist_Data,Wt='S',Pt ='Pulpmill', Name = "Softwood_Pulp_v3", Willingness = WILLING_FACTOR,Factors =Factor_Data, Typ = 3)
Hardwood_Saw.Initialize_Totals(YEARS)

print("Updating Growth Rate...")

Hardwood_Saw.Growth_Update(Growth_Data)
Hardwood_Pulp.Growth_Update(Growth_Data)
Softwood_Saw.Growth_Update(Growth_Data)
Softwood_Pulp.Growth_Update(Growth_Data)
 
# Adjusting Mixed Mills, from one Mixed mill two mills are created. a hardwood, and a softwood acordding to the availability around the mill 
Mixed = Mills_Data[Mills_Data['s_h']=='S/H'].copy()
for i in range(len(Mixed)):
  Hw = 0
  Sw = 0 
  Tt = 0
  Id1 = Mixed.iloc[i,1]
  Id2 = Mills_Data[Mills_Data['Unique_ID']==Id1].copy()
  if Mills_Data.iloc[i,2] == "Sawmill" :
    Hw = Hardwood_Saw.Total_Available(Id1,0,RADIO_MILL)
    Sw = Softwood_Saw.Total_Available(Id1,0,RADIO_MILL)
  elif Mills_Data.iloc[i,2] == "Pulpmill" :
    Hw = Hardwood_Pulp.Total_Available(Id1,0,RADIO_MILL)
    Sw = Softwood_Pulp.Total_Available(Id1,0,RADIO_MILL)
  else:
    Sw = Softwood_Pulp.Total_Available(Id1,0,RADIO_MILL)
  Tt = Hw + Sw
  Perc_Hw = Hw/Tt
  Id2['s_h'] ='S'
  Id2['Demand'] = Id2['Demand']*(1-Perc_Hw)
  Mills_Data.append(Id2)
  Mills_Data.loc[Mills_Data['Unique_ID']==Id1,('Demand')] = Mills_Data[Mills_Data['Unique_ID']==Id1].Demand*Perc_Hw
  Mills_Data.loc[Mills_Data['Unique_ID']==Id1,('s_h')] = 'H'
  
print('Updating Mills Data...')  
  
np.sum(Mills_Data.Demand)
Hardwood_Saw.Mills_Update(Mills_Data)
Hardwood_Pulp.Mills_Update(Mills_Data)
Softwood_Saw.Mills_Update(Mills_Data)
Softwood_Pulp.Mills_Update(Mills_Data)

print('Harvesting...') 

Hardwood_Pulp.Harvest_All_Mills_All_Years(YEARS,mode =HARVESTING_MODE)
Hardwood_Saw.Harvest_All_Mills_All_Years(YEARS,mode =HARVESTING_MODE)
Softwood_Pulp.Harvest_All_Mills_All_Years(YEARS,mode =HARVESTING_MODE)
Softwood_Saw.Harvest_All_Mills_All_Years(YEARS,mode =HARVESTING_MODE)

Data = {'Cost':Hardwood_Saw.__class__.Total_Cost}
pd.DataFrame(Data).to_csv(FOLDER_NAME+FILE_NAME_OUT+'Harvest_Cost.csv')

Hardwood_Saw.Total_Harvested_Update(YEARS)
Hardwood_Pulp.Total_Harvested_Update(YEARS)
Softwood_Saw.Total_Harvested_Update(YEARS)
Softwood_Pulp.Total_Harvested_Update(YEARS)
 
Hardwood_Saw.Total_Residues_Update(YEARS)
Hardwood_Pulp.Total_Residues_Update(YEARS)
Softwood_Saw.Total_Residues_Update(YEARS)
Softwood_Pulp.Total_Residues_Update(YEARS)

for y in range(YEARS+1):
  print('TOTAL HARVESTED at Hardwood_saw at',y,'  ', np.sum(Hardwood_Saw.Harvested[y].loc[:,('Harvested')]))
for y in range(YEARS+1):
  print('TOTAL HARVESTED at Hardwood_Pulp at',y,'  ', np.sum(Hardwood_Pulp.Harvested[y].loc[:,('Harvested')]))
for y in range(YEARS+1):
  print('TOTAL HARVESTED at Softwood_saw at',y,'  ', np.sum(Softwood_Saw.Harvested[y].loc[:,('Harvested')]))
for y in range(YEARS+1):
  print('TOTAL HARVESTED at softwood_Pulp at',y,'  ', np.sum(Softwood_Pulp.Harvested[y].loc[:,('Harvested')]))
 
for y in range(YEARS+1):
  Hardwood_Saw.__class__.Total_Harvested[y].to_csv(FOLDER_NAME+FILE_NAME_OUT+'TOTAL_HARVESTED_'+str(y)+'.csv')
  Hardwood_Saw.__class__.Total_Residues[y].to_csv(FOLDER_NAME+FILE_NAME_OUT+'RESIDUES_'+str(y)+'.csv')
 
print ("*********1ST STAGE TOOK", time.time() - start_time, "TO RUN")


Creating Inventories Objects and Initializing...
Updating Growth Rate...
Updating Mills Data...
Harvesting...
Cosechando Sawmill: 0
Inventory:  Hardwood_Pulp_v3  Year:  0 Mill:  59461 **Demanda: 43434490.0 Disponible 130348812.12629893 Radio 20


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:255: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:255: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:578: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.


Solution None
Cosechando Sawmill: 1
Inventory:  Hardwood_Pulp_v3  Year:  0 Mill:  65978 **Demanda: 21955605.0 Disponible 69340554.62314242 Radio 10


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:255: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:578: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.


Solution None
Cosechando Sawmill: 2
Inventory:  Hardwood_Pulp_v3  Year:  0 Mill:  80427 **Demanda: 46911808.0 Disponible 64466301.86888962 Radio 10


...

Solution None
Cosechando Sawmill: 75


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:255: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:255: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:255: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:255: SettingWithCopyWarning: 
A value is trying 

Inventory:  Softwood_Saw_v3  Year:  9 Mill:  110312 **Demanda: 26367669.0 Disponible 99286350.38457768 Radio 50


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:578: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.


Solution None
Residues: 579178.0
*********1ST STAGE YEAR:  9  TOOK 193.62398743629456 TO RUN
TOTAL HARVESTED at Hardwood_saw at 0    330537516.05590904
TOTAL HARVESTED at Hardwood_saw at 1    330537515.8027645
TOTAL HARVESTED at Hardwood_saw at 2    330537515.7550482
TOTAL HARVESTED at Hardwood_saw at 3    330537515.68124104
TOTAL HARVESTED at Hardwood_saw at 4    330537515.7905613
TOTAL HARVESTED at Hardwood_saw at 5    330537515.76230013
TOTAL HARVESTED at Hardwood_saw at 6    330537515.84639597
TOTAL HARVESTED at Hardwood_saw at 7    330537515.72284293
TOTAL HARVESTED at Hardwood_saw at 8    330537515.795661
TOTAL HARVESTED at Hardwood_saw at 9    330537515.8605925
TOTAL HARVESTED at Hardwood_saw at 10    3305375158.0733166
TOTAL HARVESTED at Hardwood_Pulp at 0    274442421.7611652
TOTAL HARVESTED at Hardwood_Pulp at 1    274442421.7796527
TOTAL HARVESTED at Hardwood_Pulp at 2    274442421.7896047
TOTAL HARVESTED at Hardwood_Pulp at 3    274442421.81365323
TOTAL HARVESTED at Hardwoo

In [ ]:
start_time = time.time()
STAGE = 2
Indice1 = (Cand_Dist['DEST']==AIRPORT_LOCATION) & (Cand_Dist['DIST'] < 150)
ma = Cand_Dist.loc[Indice1,('ORIG')]
#print('Candidates:', len(ma))
ma.reset_index(inplace = True, drop = True)

#ma = Cand_Dist['ORIG'].unique()
print('Candidates:', len(ma))


Residues_Inv = Inventory(Hardwood_Saw_Data,Dist_Data,Wt='H',Pt ='Sawmill', Name = "Hardwood_Saw", Willingness = WILLING_FACTOR,Factors =Factor_Data,Typ =0,St = STAGE)
Residues_Inv.Candidates = ma
Residues_Inv.Initialize_Totals(YEARS)
Residues_Inv.Load_Residues(YEARS)
Residues_Inv.Optimal_Location_Total2(YEARS,STAGE, REF_DEMAND)

print('Costs of Candidates:',Residues_Inv.RefCost)
Min_Pos =Residues_Inv.RefCost.index(min(Residues_Inv.RefCost))
print('Minimum costs at:',ma[Min_Pos])
print ("*********2ND STAGE TOOK", time.time() - start_time, "TO RUN") 
